<a href="https://colab.research.google.com/github/reignslau/CSE310-winter/blob/main/%E5%A4%8D%E5%88%B6%E2%80%9Cstarter_housing_ipynb%E2%80%9D%E7%9A%84%E5%89%AF%E6%9C%AC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Data Exploration

In [1]:
import pandas as pd
import numpy as np
from  xgboost XGBRegressor
from sklearn.model_selection import train_test_split
housing = pd.read_csv('https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing.csv')
housing.head()

id             date  bedrooms  bathrooms  sqft_living  sqft_lot  \
0  1565930130  20141104T000000         4       3.25         3760      4675   
1  3279000420  20150115T000000         3       1.75         1460      7800   
2   194000575  20141014T000000         4       1.00         1340      5800   
3  2115510160  20141208T000000         3       1.75         1440      8050   
4  7522500005  20140815T000000         2       1.50         1780      4750   

   floors  waterfront  view  condition  ...  sqft_above  sqft_basement  \
0     2.0           0     0          3  ...        2740           1020   
1     1.0           0     0          2  ...        1040            420   
2     1.5           0     2          3  ...        1340              0   
3     1.0           0     0          3  ...        1440              0   
4     1.0           0     0          4  ...        1080            700   

   yr_built  yr_renovated  zipcode      lat     long  sqft_living15  \
0      2007             0    98038  47.3862 -122.048           3280   
1      1979             0    98023  47.3035 -122.382           1310   
2      1914             0    98116  47.5658 -122.389           1900   
3      1985             0    98023  47.3187 -122.390           1790   
4      1947             0    98117  47.6859 -122.395           1690   

   sqft_lot15     price  
0        4033  429900.0  
1        7865  233000.0  
2        5800  455000.0  
3        7488  258950.0  
4        5962  555000.0  

[5 rows x 21 columns]

In [2]:
import pandas as pd
import math

# Function to calculate Haversine distance.
def haversine_distance(lat1, lon1, lat2, lon2):
    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = math.sin(dlat / 2) ** 2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2) ** 2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))

    # Radius of Earth in miles
    R = 3958.8  # Use 3958.8 for miles

    distance = R * c

    return distance



In [3]:
# Locations of interest
bellevue_lat, bellevue_lon = 47.6104, -122.2007
medina_lat, medina_lon = 47.6248, -122.2361
mercer_lat, mercer_lon = 47.5707, -122.2221 #Mercer Park

# Calculate distances and create new columns
housing['dist_bellevue'] = housing.apply(lambda row: haversine_distance(bellevue_lat, bellevue_lon, row['lat'], row['long']), axis=1)
housing['dist_medina'] = housing.apply(lambda row: haversine_distance(medina_lat, medina_lon, row['lat'], row['long']), axis=1)
housing['dist_mercer'] = housing.apply(lambda row: haversine_distance(mercer_lat, mercer_lon, row['lat'], row['long']), axis=1)
housing.head()

id             date  bedrooms  bathrooms  sqft_living  sqft_lot  \
0  1565930130  20141104T000000         4       3.25         3760      4675   
1  3279000420  20150115T000000         3       1.75         1460      7800   
2   194000575  20141014T000000         4       1.00         1340      5800   
3  2115510160  20141208T000000         3       1.75         1440      8050   
4  7522500005  20140815T000000         2       1.50         1780      4750   

   floors  waterfront  view  condition  ...  yr_renovated  zipcode      lat  \
0     2.0           0     0          3  ...             0    98038  47.3862   
1     1.0           0     0          2  ...             0    98023  47.3035   
2     1.5           0     2          3  ...             0    98116  47.5658   
3     1.0           0     0          3  ...             0    98023  47.3187   
4     1.0           0     0          4  ...             0    98117  47.6859   

      long  sqft_living15  sqft_lot15     price  dist_bellevue  dist_medina  \
0 -122.048           3280        4033  429900.0      17.052220    18.677836   
1 -122.382           1310        7865  233000.0      22.833952    23.222464   
2 -122.389           1900        5800  455000.0       9.300320     8.208159   
3 -122.390           1790        7488  258950.0      22.009095    22.337724   
4 -122.395           1690        5962  555000.0      10.440773     8.515498   

   dist_mercer  
0    15.119782  
1    19.917026  
2     7.788002  
3    19.097704  
4    11.321486  

[5 rows x 24 columns]

In [4]:
features = ["bedrooms", "bathrooms", "sqft_living", "sqft_lot", "floors", "waterfront",
            "view", "sqft_above", "sqft_basement", "yr_built", "yr_renovated", "zipcode",
            "lat", "long", "sqft_living15", "sqft_lot15", 'dist_mercer', 'dist_medina', 'dist_bellevue']

for i in features:
    housing[i].dtype


In [5]:
housing['zipcode'].unique()

array([98038, 98023, 98116, 98117, 98034, 98065, 98031, 98075, 98028,
       98103, 98004, 98166, 98077, 98008, 98006, 98199, 98052, 98136,
       98108, 98055, 98027, 98058, 98144, 98115, 98168, 98102, 98042,
       98059, 98002, 98155, 98072, 98001, 98112, 98007, 98177, 98074,
       98119, 98011, 98014, 98106, 98045, 98033, 98125, 98133, 98053,
       98122, 98022, 98178, 98148, 98019, 98010, 98070, 98056, 98030,
       98188, 98029, 98107, 98105, 98198, 98003, 98118, 98126, 98040,
       98092, 98032, 98146, 98024, 98005, 98039, 98109])

In [6]:
import plotly.express as px

housing['date'] = pd.to_datetime(housing['date'], format='%Y%m%dT%H%M%S')
housing['year'] = housing['date'].dt.year
fig = px.scatter(housing, x='long', y='lat', color='price', facet_col='year',
                 labels={"price": "Price", "long": "Longitude", "lat": "Latitude"},
                 title="House Value by Location")
fig.show()

In [7]:
# prompt: show the average price different between 2014 and 2015

average_price_2014 = housing[housing['year'] == 2014]['price'].mean()
average_price_2015 = housing[housing['year'] == 2015]['price'].mean()
price_difference = average_price_2015 - average_price_2014
print(f"The average price difference between 2014 and 2015 is: {price_difference}")


The average price difference between 2014 and 2015 is: 5555.525423276122


In [8]:
# prompt: create a table to show the top priced homes in 2015 vs 2014

import pandas as pd
top_priced_homes_2015 = housing.loc[(housing['year'] == 2015)].sort_values(by='price', ascending=False).head(10)
top_priced_homes_2014 = housing.loc[(housing['year'] == 2014)].sort_values(by='price', ascending=False).head(10)

tables = pd.concat([top_priced_homes_2015, top_priced_homes_2014], axis=1, keys=['2015', '2014'])
print(tables)


               2015                                                            \
                 id       date bedrooms bathrooms sqft_living sqft_lot floors   
366    8.907500e+09 2015-04-13      5.0      5.00      8000.0  23985.0    2.0   
3426   7.558700e+09 2015-04-13      6.0      6.00      7390.0  24829.0    2.0   
15201  6.065300e+09 2015-05-06      5.0      6.00      7440.0  21540.0    2.0   
379    4.389201e+09 2015-05-11      5.0      3.75      5020.0   8694.0    2.0   
6210   9.253900e+09 2015-01-07      5.0      4.50      4850.0  10584.0    2.0   
4858   1.118000e+09 2015-05-08      4.0      4.00      4260.0  11765.0    2.0   
4447   3.126059e+09 2015-03-03      4.0      3.50      4730.0  47870.0    1.0   
8903   9.808100e+09 2015-04-02      5.0      3.75      5350.0  15360.0    1.0   
2174   8.964801e+09 2015-01-09      3.0      3.25      4560.0  13363.0    1.0   
9040   1.732801e+09 2015-02-12      5.0      3.00      4150.0   7500.0    2.5   
8753            NaN        N

# Model

get X and y values ready for computation


In [9]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
import xgboost as xgb
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error

# Split features and target variable
X = housing[["bedrooms", "bathrooms", "sqft_living", "sqft_lot", "floors", "waterfront",
            "view", "sqft_above", "sqft_basement", "yr_built", "yr_renovated", "zipcode",
            "lat", "long", "sqft_living15", "sqft_lot15", 'dist_mercer', 'dist_medina', 'dist_bellevue', 'year']]
y = housing["price"]

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

Figure out the best parameters for the model using a Grid Search. 1 was the initial grid, going down to 3 which is the final grid. If you want to run grid 1, you can, but it'll take 30 mins

In [10]:
from xgboost import XGBRegressor
from sklearn.model_selection import GridSearchCV

param_grid_1 = {
    'max_depth' : [3,4,5],              # This parameter specifies the maximum depth of a tree. Deeper trees can capture more complex patterns in the data but are more prone to overfitting.
    'learning_rate' : [.1,.01,.05],     # Also known as the "eta" parameter, this controls the step size shrinkage used to prevent overfitting. Lower values make the model more robust but require more boosting rounds to achieve the same effect.
    'gamma' : [0,.25,1.0],              # This parameter specifies the minimum loss reduction required to make a further partition on a leaf node of the tree. Higher values lead to more conservative models.
    'reg_lambda' : [0,1.0,10.0],        # Also known as the L2 regularization term, this parameter controls the regularization strength on leaf weights. It helps prevent overfitting by penalizing large weights.
    'scale_pos_weight' : [1,3,5],       # This parameter helps with imbalanced datasets by scaling the positive weight, which is useful for highly skewed classes.
    'colsample_bytree': [0.5],          # This parameter specifies the fraction of features to be randomly sampled for each tree. It helps prevent overfitting by introducing randomness.
    'subsample': [0.9]                  # This parameter specifies the fraction of observations to be randomly sampled for each tree. It helps prevent overfitting by introducing randomness.
}
# Output: Best parameters found:  {'colsample_bytree': 0.5, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 5, 'reg_lambda': 0, 'scale_pos_weight': 1, 'subsample': 0.9}
# Lowest RMSE found:  124336.74785211888

param_grid_2 = {
    'max_depth' : [5,6,7],
    'learning_rate' : [0.3, 0.2, 0.1],
    'gamma' : [0],
    'reg_lambda' : [0],
    'scale_pos_weight' : [1.0, 0.1, 0.05],
    'colsample_bytree': [0.5],
    'subsample': [0.9]
}
# Output: Best parameters found:  {'colsample_bytree': 0.5, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 7, 'reg_lambda': 0, 'scale_pos_weight': 1.0, 'subsample': 0.9}
# Lowest RMSE found:  124254.65966121879

param_grid_3 = {
    'max_depth' : [7,8,9,10],
    'learning_rate' : [0.1],
    'gamma' : [0],
    'reg_lambda' : [0],
    'scale_pos_weight' : [1.0],
    'colsample_bytree': [0.5],
    'subsample': [0.9]
}
# Output: Best parameters found:  {'colsample_bytree': 0.5, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 8, 'reg_lambda': 0, 'scale_pos_weight': 1.0, 'subsample': 0.9}
# Lowest RMSE found:  123281.5941171983

param_grid_4 = {
    'max_depth' : [8],
    'learning_rate' : [0.1],
    'gamma' : [0],
    'reg_lambda' : [0],
    'scale_pos_weight' : [1.0],
    'colsample_bytree': [0.6,0.5,0.4],
    'subsample': [1.0,0.9,0.8]
}
# Output: Best parameters found:  {'colsample_bytree': 0.6, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 8, 'reg_lambda': 0, 'scale_pos_weight': 1.0, 'subsample': 0.9}
# Lowest RMSE found:  123025.5328594299

param_grid_5 = {
    'max_depth' : [8],
    'learning_rate' : [0.1],
    'gamma' : [0],
    'reg_lambda' : [0],
    'scale_pos_weight' : [1.0],
    'colsample_bytree': [0.8,0.7,0.6],
    'subsample': [0.9]
}
# Output: Best parameters found:  {'colsample_bytree': 0.6, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 8, 'reg_lambda': 0, 'scale_pos_weight': 1.0, 'subsample': 0.9}
# Lowest RMSE found:  123025.5328594299

param_grid_6 = {
    'max_depth': [8],          # Testing different maximum tree depths
    'learning_rate': [0.1],              # Using a fixed learning rate
    'gamma': [0],                        # No minimum loss reduction required for further partitioning
    'reg_lambda': [0],                   # No L2 regularization
    'scale_pos_weight': [1.0],           # No scaling of positive weight
    'colsample_bytree': [0.6],           # Using 50% of features for each tree
    'colsample_bynode': [0.5, 0.7, 0.9], # Testing different colsample_bynode values
    'subsample': [0.9],                  # Using 90% of data for each tree
    'min_child_weight': [1, 5, 10],      # Testing different minimum child weights
    'alpha': [0, 0.1, 1],                # Testing different L1 regularization strengths
    'n_estimators': [100, 200, 300]      # Testing different number of boosting rounds
}
# Output: Best parameters found:  {'alpha': 0.1, 'colsample_bynode': 0.5, 'colsample_bytree': 0.6, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 8, 'min_child_weight': 5, 'n_estimators': 300, 'reg_lambda': 0, 'scale_pos_weight': 1.0, 'subsample': 0.9}
# Lowest RMSE found:  119665.57116681022

param_grid_7 = {
    'max_depth': [8],
    'learning_rate': [0.1],
    'gamma': [0],
    'reg_lambda': [0],
    'scale_pos_weight': [1.0],
    'colsample_bytree': [0.6],
    'colsample_bynode': [0.5, 0.4, 0.3],
    'subsample': [0.9],
    'min_child_weight': [4, 5, 6],
    'alpha': [0.1],
    'n_estimators': [300, 400, 500]
}
# Output: Best parameters found:  {'alpha': 0.1, 'colsample_bynode': 0.5, 'colsample_bytree': 0.6, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 8, 'min_child_weight': 5, 'n_estimators': 300, 'reg_lambda': 0, 'scale_pos_weight': 1.0, 'subsample': 0.9}
# Lowest RMSE found:  119665.57116681022

param_grid_8 = {
    'max_depth': [8],
    'learning_rate': [0.1],
    'gamma': [0, 0.5, 1.0],               # Different values for gamma
    'reg_lambda': [0, 1.0, 2.0],          # Different values for reg_lambda
    'scale_pos_weight': [1.0],
    'colsample_bytree': [0.6],
    'colsample_bynode': [0.5, 0.4, 0.3],
    'subsample': [0.9],
    'min_child_weight': [4, 5, 6],
    'alpha': [0.1, 0.5, 1.0],             # Different values for alpha
    'n_estimators': [300, 400, 500]
}
# Grid 6 and 7 is overfit DO NOT USE

In [11]:
# Create the XGBRegressor model
model = XGBRegressor(random_state=42, booster='gbtree', eval_metric='rmse')

WARNING: If this code section is not commented out, the runtime will be very slow. This section was purely to figure out the parameters

In [12]:
# Create GridSearchCV object
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_1, cv=5, scoring='neg_mean_squared_error', verbose=2)
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_2, cv=5, scoring='neg_mean_squared_error', verbose=2)
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_3, cv=5, scoring='neg_mean_squared_error', verbose=2)
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_4, cv=5, scoring='neg_mean_squared_error', verbose=2)
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_5, cv=5, scoring='neg_mean_squared_error', verbose=2)
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_6, cv=5, scoring='neg_mean_squared_error', verbose=2)
# grid_search = GridSearchCV(estimator=model, param_grid=param_grid_7, cv=5, scoring='neg_mean_squared_error', verbose=2)

# Fit the model
#grid_search.fit(X_train, y_train, eval_set=[(X_test, y_test)])

# Get the best parameters and the best score
#print("Best parameters found: ", grid_search.best_params_)
#print("Lowest RMSE found: ", (-grid_search.best_score_) ** 0.5)

Random Grid Search

In [13]:
from sklearn.model_selection import RandomizedSearchCV
# Randomized search with cross-validation
random_search = RandomizedSearchCV(estimator=model,
                                   param_distributions=param_grid_8,
                                   n_iter=100,      # Number of parameter settings that are sampled
                                   cv=5,            # 5-fold cross-validation
                                   verbose=2,
                                   random_state=42, # Set random seed for reproducibility
                                   n_jobs=-1)       # Use all available cores

# Fit the random search model
random_search.fit(X_train, y_train)

# Best parameters
print("Best parameters found: ", random_search.best_params_)

# Best estimator
best_xgb = random_search.best_estimator_

# Evaluate the best model
best_score = best_xgb.score(X_test, y_test)
print("Best score on test data: ", best_score)

Fitting 5 folds for each of 100 candidates, totalling 500 fits
Best parameters found:  {'subsample': 0.9, 'scale_pos_weight': 1.0, 'reg_lambda': 0, 'n_estimators': 300, 'min_child_weight': 5, 'max_depth': 8, 'learning_rate': 0.1, 'gamma': 1.0, 'colsample_bytree': 0.6, 'colsample_bynode': 0.5, 'alpha': 0.1}
Best score on test data:  0.8885981829796612


Insert best parameters, and fit the model! :)

In [14]:
# @title Default title text
# Train the model (XGBoost)
from xgboost import XGBRegressor

best_params = {
    'colsample_bytree': 0.6,
    'gamma': 0,
    'learning_rate': 0.1,
    'max_depth': 8,
    'reg_lambda': 0,
    'scale_pos_weight': 1.0,
    'subsample': 0.9,
}

# Update the model with the best parameters
model = XGBRegressor(random_state=42, booster='gbtree',
                     verbosity=1, eval_metric='rmse', **best_params) #rmse
model.fit(X_train, y_train,
          eval_set=[(X_test, y_test)])

[0]	validation_0-rmse:360093.89120
[1]	validation_0-rmse:336264.53135
[2]	validation_0-rmse:313357.80739
[3]	validation_0-rmse:294488.16311
[4]	validation_0-rmse:275539.01472
[5]	validation_0-rmse:260690.77927
[6]	validation_0-rmse:244279.77874
[7]	validation_0-rmse:230866.06048
[8]	validation_0-rmse:219532.15651
[9]	validation_0-rmse:208049.84997
[10]	validation_0-rmse:200338.61139
[11]	validation_0-rmse:192226.77315
[12]	validation_0-rmse:185644.58751
[13]	validation_0-rmse:179584.20673
[14]	validation_0-rmse:174130.85044
[15]	validation_0-rmse:169832.30322
[16]	validation_0-rmse:165731.42179
[17]	validation_0-rmse:162474.90395
[18]	validation_0-rmse:158993.78004
[19]	validation_0-rmse:156499.46997
[20]	validation_0-rmse:154294.06602
[21]	validation_0-rmse:152386.34694
[22]	validation_0-rmse:150520.84806
[23]	validation_0-rmse:148567.82976
[24]	validation_0-rmse:147037.80454
[25]	validation_0-rmse:145936.44536
[26]	validation_0-rmse:145085.15489
[27]	validation_0-rmse:144209.53761
[2

XGBRegressor(base_score=None, booster='gbtree', callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.6, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric='rmse', feature_types=None,
             gamma=0, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.1, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=8, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=None, n_jobs=None,
             num_parallel_tree=None, random_state=42, ...)

Run the model, get the predictions

In [15]:
# Make predictions
y_pred = model.predict(X_test)

# Calculate RMSE
rmse = mean_squared_error(y_test, y_pred, squared=False)
print("RMSE:", rmse)

# Feature Importance Analysis (XGBoost has built-in feature importance)
importance = model.feature_importances_
feature_importance_df = pd.DataFrame({"Feature": X_test.columns, "Importance": importance})
feature_importance_df = feature_importance_df.sort_values(by="Importance", ascending=False)
print(feature_importance_df)

RMSE: 134356.7494706343
          Feature  Importance
6            view    0.134144
5      waterfront    0.111308
7      sqft_above    0.109065
12            lat    0.097692
2     sqft_living    0.086657
17    dist_medina    0.084740
14  sqft_living15    0.062618
18  dist_bellevue    0.057834
8   sqft_basement    0.044525
4          floors    0.038873
13           long    0.027470
16    dist_mercer    0.027384
1       bathrooms    0.027257
11        zipcode    0.019722
15     sqft_lot15    0.018691
3        sqft_lot    0.013371
9        yr_built    0.013188
10   yr_renovated    0.012151
19           year    0.009497
0        bedrooms    0.003814


Generate the confusion matrix

In [16]:
import plotly.express as px
import numpy as np

# Calculate residuals
residuals = y_pred - y_test

# Create DataFrame with actual, predicted, and residuals
result_df = pd.DataFrame({'Actual': y_test, 'Predicted': y_pred, 'Residuals': residuals})

# Define color scale using "Viridis"
color_scale = 'Viridis'

# Create scatter plot
fig = px.scatter(result_df, x='Actual', y='Predicted', color='Residuals', color_continuous_scale=color_scale,
                 trendline='ols', labels={'Actual': 'Actual', 'Predicted': 'Predicted', 'Residuals': 'Residuals'},
                 title='Actual vs Predicted Values with Residual Color Scale')
fig.update_layout(
    xaxis_title='Actual',
    yaxis_title='Predicted',
    title={
        'text': 'Actual vs Predicted Values with Residual Color Scale',
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
fig.show()

# Holdout Dataset Predictions

In [17]:
holdout_MINI = pd.read_csv("https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing_holdout_test_mini.csv")

# Locations of interest
bellevue_lat, bellevue_lon = 47.6104, -122.2007
medina_lat, medina_lon = 47.6248, -122.2361
mercer_lat, mercer_lon = 47.5707, -122.2221

# Add year column
holdout_MINI['date'] = pd.to_datetime(housing['date'], format='%Y%m%dT%H%M%S')
holdout_MINI['year'] = housing['date'].dt.year


# Calculate distances and create new columns
holdout_MINI['dist_bellevue'] = housing.apply(lambda row: haversine_distance(bellevue_lat, bellevue_lon, row['lat'], row['long']), axis=1)
holdout_MINI['dist_medina'] = housing.apply(lambda row: haversine_distance(medina_lat, medina_lon, row['lat'], row['long']), axis=1)
holdout_MINI['dist_mercer'] = housing.apply(lambda row: haversine_distance(mercer_lat, mercer_lon, row['lat'], row['long']), axis=1)


X_new = holdout_MINI[["bedrooms", "bathrooms", "sqft_living", "sqft_lot", "floors", "waterfront",
            "view", "sqft_above", "sqft_basement", "yr_built", "yr_renovated", "zipcode",
            "lat", "long", "sqft_living15", "sqft_lot15", 'dist_mercer', 'dist_medina', 'dist_bellevue', 'year']]

# Make predictions with the new data
y_new_pred = model.predict(X_new)

# Make a new column in bank_holdout_MINI for the predictions
holdout_MINI['y_pred'] = y_new_pred
print(holdout_MINI['y_pred'])
df = pd.DataFrame()

df["predictions"] = y_new_pred

df.to_csv("team5-module3-predictions.csv", index=False)
holdout_MINI['y_pred'].to_csv('team5-module3-predictions.csv', index=False)

0     407289.250000
1     463573.500000
2     204642.453125
3     367854.500000
4     411500.656250
          ...      
76    604226.125000
77    663831.875000
78    632802.812500
79    292057.343750
80    642921.812500
Name: y_pred, Length: 81, dtype: float32


# Data Analysis and Plots


PLOT FOR PRICE MAP (NOT USING)

In [18]:
import plotly.express as px
#Heat map showing price based on location
px.scatter(housing, x='long', y='lat', color='price')

In [19]:
# prompt: make a chart to show the importance of the dist_mercer and dist_medina had on the model

fig = px.scatter(housing, x='dist_mercer', y='price', trendline='ols', color='dist_mercer', labels={'dist_mercer': 'Distance from Mercer Park (miles)', 'price': 'Price', 'dist_medina': 'Distance from Medina (miles)'},
                 title='Relationship between Distance from Mercer Park and Price')
fig.update_layout(
    xaxis_title='Distance from Mercer Park (miles)',
    yaxis_title='Price',
    title={
        'text': 'Relationship between Distance from Mercer Park and Price',
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
fig.show()

fig = px.scatter(housing, x='dist_medina', y='price', trendline='ols', color='dist_medina', labels={'dist_medina': 'Distance from Medina (miles)', 'price': 'Price', 'dist_mercer': 'Distance from Mercer Park (miles)'},
                 title='Relationship between Distance from Medina and Price')
fig.update_layout(
    xaxis_title='Distance from Medina (miles)',
    yaxis_title='Price',
    title={
        'text': 'Relationship between Distance from Medina and Price',
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
fig.show()

View charts to see why the view was an important feature.

1) Looked at which features were more important

2) See the average price per view

3) See the average price with/without waterfront

4) See the impact waterfront and view had on average price, based on one illustrating the average price by view score for waterfront properties and the other illustrating the average price by view score for non-waterfront properties

In [20]:
import plotly.express as px

# Create a bar chart showing the impact of the 'view' feature on the model
fig = px.bar(feature_importance_df, x='Feature', y='Importance', color='Feature',
             title='Feature Importance for XGBoost Model',
             labels={'Feature': 'Feature', 'Importance': 'Importance'},
             color_discrete_map={
                 'bedrooms': 'blue',
                 'bathrooms': 'orange',
                 'sqft_living': 'green',
                 'sqft_lot': 'red',
                 'floors': 'purple',
                 'waterfront': 'brown',
                 'view': 'black',
                 'sqft_above': 'pink',
                 'sqft_basement': 'gray',
                 'yr_built': 'cyan',
                 'yr_renovated': 'yellow',
                 'zipcode': 'magenta',
                 'lat': 'violet',
                 'long': 'indigo',
                 'sqft_living15': 'gold',
                 'sqft_lot15': 'silver',
                 'dist_mercer': 'teal',
                 'dist_medina': 'navy',
                 'dist_bellevue': 'turquoise',
                 'year': 'olive'
             })
fig.update_layout(
    xaxis_title='Feature',
    yaxis_title='Importance on the Model',
    title={
        'text': 'Feature Importance for Reddic Model',
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis=dict(tickformat="%"))
fig.show()


In [21]:
# Create a bar chart of the average price for each view category
import plotly.express as px

average_price_by_view = housing.groupby('view')['price'].mean().reset_index()
fig = px.bar(average_price_by_view, x='view', y='price',
             title='Average Price by View',
             labels={'view': 'View Category', 'price': 'Average Price'})

fig.update_traces(text=average_price_by_view['price'].round(2), textposition='outside')
fig.update_layout(
    xaxis_title='View Category',
    yaxis_title='Average Price',
    title={
        'text': 'Average Price by View',
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
fig.show()



In [22]:
# Create a bar chart of the average price for each waterfront category
import plotly.express as px

average_price_by_waterfront = housing.groupby('waterfront')['price'].mean().reset_index()
fig = px.bar(average_price_by_waterfront, x='waterfront', y='price',
             title='Average Price by Waterfront',
             labels={'waterfront': 'Waterfront', 'price': 'Average Price'})

fig.update_traces(text=average_price_by_waterfront['price'].round(2), textposition='outside')
fig.update_layout(
    xaxis_title='Waterfront',
    yaxis_title='Average Price',
    title={
        'text': 'Average Price by Waterfront',
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'}
)
fig.show()



In [23]:
import plotly.graph_objects as go

# Calculate the average price for waterfront properties by view score
average_price_waterfront = housing[housing['waterfront'] == 1].groupby('view')['price'].mean()

# Calculate the average price for non-waterfront properties by view score
average_price_non_waterfront = housing[housing['waterfront'] == 0].groupby('view')['price'].mean()

# Create figure
fig = go.Figure()

# Add trace for waterfront properties
fig.add_trace(go.Bar(
    x=average_price_waterfront.index,
    y=average_price_waterfront,
    name='Waterfront',
    marker_color='blue'
))

# Add trace for non-waterfront properties
fig.add_trace(go.Bar(
    x=average_price_non_waterfront.index,
    y=average_price_non_waterfront,
    name='Non-Waterfront',
    marker_color='orange'
))

# Update layout
fig.update_layout(
    title='Average Price by View Score for Waterfront and Non-Waterfront Properties',
    xaxis_title='View Score',
    yaxis_title='Average Price',
    barmode='group'
)

fig.show()
